In [12]:
# Load packages
import warnings
warnings.filterwarnings("ignore")
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup
import json
import time
import pandas as pd
from uuid import uuid4
import csv 
import os
import re

In [2]:
codes = pd.read_excel("codes.xlsx", dtype={'Code': str})

In [55]:
codes

Code State
0   35004    AL
1   99501    AK
2   85001    AZ
3   71601    AR
4   90001    CA
5   80001    CO
6   06001    CT
7   19701    DE
8   32003    FL
9   30002    GA
10  96701    HI
11  83201    ID
12  60001    IL
13  46001    IN
14  50001    IA
15  66002    KS
16  40003    KY
17  70001    LA
18  03901    ME
19  20588    MD
20  01001    MA
21  48001    MI
22  55001    MN
23  38601    MS
24  63001    MO
25  59001    MT
26  68001    NE
27  88901    NV
28  03031    NH
29  07001    NJ
30  87001    NM
31  00501    NY
32  27006    NC
33  58001    ND
34  43001    OH
35  73001    OK
36  97001    OR
37  15001    PA
38  02801    RI
39  29001    SC
40  57001    SD
41  37010    TN
42  73301    TX
43  84001    UT
44  05001    VT
45  20101    VA
46  98001    WA
47  24701    WV
48  53001    WI
49  82001    WY

In [45]:
# Start Chrome
driver = webdriver.Chrome(ChromeDriverManager().install())

In [4]:
def write_dealer(dealers_data):
    with open(os.path.join('F:\Dealer_Reviews', 'dealers.csv'), "a", encoding="utf-8") as csv_file: 
        writer = csv.writer(csv_file, delimiter = ";")
        print('writing dealer into file') 
        #for contents in dealers_data:
        writer.writerow([dealers_data['dealer_id'], dealers_data['state'], dealers_data['dealer_link'], 
                         dealers_data['avg_rating'], dealers_data['nr_reviews'], dealers_data['inventory_size'], 
                         dealers_data['inventory_link'], dealers_data['registration_date']])

In [5]:
def write_car(cars_data):
    with open(os.path.join('F:\Dealer_Reviews', 'cars.csv'), "a", encoding="utf-8") as csv_file: 
        writer = csv.writer(csv_file, delimiter = ";")
        print('writing car into file') 
        #for contents in dealers_data:
        writer.writerow([cars_data['dealer_id'], cars_data['title'], cars_data['mileage'], cars_data['price']])

In [6]:
def write_review(reviews_data):
    with open(os.path.join('F:\Dealer_Reviews', 'reviews.csv'), "a", encoding="utf-8") as csv_file: 
        writer = csv.writer(csv_file, delimiter = ";")
        print('writing review into file') 
        #for contents in dealers_data:
        writer.writerow([reviews_data['dealer_id'], reviews_data['review_score'], reviews_data['review_title'], 
                         reviews_data['review_date'], reviews_data['review_text'], reviews_data['cust_service'], 
                         reviews_data['buying_process'], reviews_data['repair_quality'], reviews_data['facilities'], 
                         reviews_data['experience'], reviews_data['recommend'], reviews_data['purchase_type'],
                        reviews_data['purchase']])

In [7]:
def calculate(nr_reviews, inventory):
    if pd.isna(inventory) is True:
        limit = nr_reviews
    else:
        if inventory > nr_reviews:
            limit = nr_reviews
        else:
            limit = round(((inventory*8)/2)+inventory)
            if limit > nr_reviews:
                limit = nr_reviews
    return limit    

In [65]:
def dealers(soup, i):
        dealer = soup.find(attrs = {"id": "dealers-list"}).find_all(attrs ={"class": "sds-container dealer-card"})[i]
        #get dealer page link
        link = dealer.find('a')['href']
        dealer_link = 'https://www.cars.com' + str(link)
        
        #get dealer average rating
        rating_class = dealer.find(attrs ={"class": "sds-rating"})
        if rating_class is None:
            avg_rating = "Not rated"
        else:    
            avg_rating = rating_class.find(attrs ={"class": "sds-rating__count"})
            if avg_rating is None:
                avg_rating = "Not rated"
            else:
                avg_rating = rating_class.find(attrs ={"class": "sds-rating__count"}).get_text()
        
        #get total number of reviews
        nr_reviews = dealer.find(attrs ={"class": "sds-rating__link sds-button-link"})
        if nr_reviews is None:
            nr_reviews = float("NaN")
        else: 
            nr_reviews = nr_reviews.get_text()
            nr_reviews = nr_reviews[1:-1]
            nr_reviews = nr_reviews.split(' ')[0]
            nr_reviews = nr_reviews.replace(',', '')
            nr_reviews = int(nr_reviews)
        
        #open dealer page
        url = dealer_link
        driver.get(url)
        res = driver.page_source.encode('utf-8')
        soup = BeautifulSoup(res, "html.parser")
        
        #inventory size
        inventory_size = soup.find(attrs = {'data-linkname': "dealer-inventory-all"})
        if inventory_size is None:
            inventory_size = float("NaN")
        else:
            inventory_size = inventory_size.get_text()
            inventory_size = [int(s) for s in re.findall(r'\b\d+\b', inventory_size)][0]
        
        #inventory link
        inventory_link = soup.find(attrs = {"data-linkname": "dealer-inventory-all"})
        if inventory_link is None:
            inventory_link = float("NaN")
        else: 
            inventory_link = inventory_link['href']
            inventory_link = 'https://www.cars.com' + str(inventory_link)
        
        #registration date
        registration = soup.find(attrs = {"class": "dealer-cars-history"})
        if registration is None:
            registration = float("NaN")
        else:    
            registration = registration.find("strong").get_text()
        
        data = {'dealer_link': dealer_link,
            'avg_rating': avg_rating,
            'nr_reviews': nr_reviews,
            'inventory_size': inventory_size,
            'inventory_link': inventory_link,    
            'registration_date': registration}
        
        return data

In [9]:
def cars(car_list, i):
            car = car_list[i]
            #title of car
            title = car.find(attrs = {"class": "title"}).get_text()
            #mileage
            mileage = car.find(attrs = {"class": "mileage"})
            if mileage is None:
                mileage = float("NaN")
            else:    
                mileage = car.find(attrs = {"class": "mileage"}).get_text()
                mileage = mileage.split(' ')[0]
                mileage = mileage.replace(',', '')
                mileage = int(mileage)
            #price
            price = car.find(attrs = {"class": "primary-price"}).get_text()
            data = {'title': title,
                    'mileage': mileage,
                    'price': price}
            
            return data

In [78]:
a = 'jksogr,page=3/lgnpiwergpo'
a.replace('page=' + str(current_page), 'page='+ str(current_page+1))

'jksogr,page=4/lgnpiwergpo'

In [85]:
def reviews(soup, i, current_page, url):
    review = soup.find(attrs = {"class": "reviews-collection"})
    if review is None:
        driver.get(url)
        res = driver.page_source.encode('utf-8')
        soup = BeautifulSoup(res, "html.parser")
        review = soup.find(attrs = {"class": "reviews-collection"})
        if review is None:
            url = url.replace("page="+ str(current_page), "page=" + str(current_page+1))
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")
            review = soup.find(attrs = {"class": "reviews-collection"}).find_all(attrs = {"class": "sds-container consumer-review-container"})[i]
            current_page = current_page + 1
    else:    
        review = soup.find(attrs = {"class": "reviews-collection"}).find_all(attrs = {"class": "sds-container consumer-review-container"})[i]

    review_score = review.find(attrs = {"class": "sds-rating__count"})
    if review_score is None:
        review_score = 0
    else:
        review_score = review.find(attrs = {"class": "sds-rating__count"}).get_text()
    
    review_title = review.find(attrs = {"class": "sds-heading--7 title"}).get_text()
    
    review_date = review.find(attrs = {"class": "review-byline review-section"})
    review_date = review_date.find("div").get_text()
    
    review_text = review.find(attrs = {"class": "review-body"}).get_text()
    
    breakdown = review.find(attrs = {"class": "sds-definition-list review-breakdown--list"})
    breakdown = breakdown.find_all("li")
    cust_service = breakdown[0].find_all("span")[1].get_text()
    buying_process = breakdown[1].find_all("span")[1].get_text()
    repair_quality = breakdown[2].find_all("span")[1].get_text()
    facilities = breakdown[3].find_all("span")[1].get_text()
    experience = breakdown[4].find_all("span")[1].get_text()
    recommendation = review.find(attrs = {"class": "sds-list sds-list--unordered review-reasons"}).find_all("li")
    
    #check if they recommend, the type of purchase or if they bought a car
    if recommendation[0].find("strong").get_text() == 'Does':
        recommend = 'yes'
    else:
        recommend = 'no'

    if recommendation[1].find("strong").get_text() == 'new':
        purchase_type = 'new'
    elif recommendation[1].find("strong").get_text() == 'used':
        purchase_type = 'used'  
    elif recommendation[1].find("strong").get_text() == 'service or repair':   
        purchase_type = 'repair'

    if len(recommendation) < 3:
        purchase = 'no purchase'
    elif recommendation[2].find("strong").get_text() == 'Did':
        purchase = 'yes'
    else:
        purchase = 'no'
    
    data = {'review_score': review_score,
            'review_title': review_title,
            'review_date': review_date,
            'review_text': review_text,
            'cust_service': cust_service,
            'buying_process': buying_process,
            'repair_quality': repair_quality,
            'facilities': facilities,
            'experience': experience,
            'recommend': recommend,
            'purchase_type': purchase_type,
            'purchase': purchase}
    return data

In [97]:
### iteration through all 50 states
start_time = time.time()
for x in range(40,50):
    i = codes['Code'][x]
    url = "https://www.cars.com/dealers/buy/?makes[]=&maximum_distance=99999&page=1&page_size=100&zip=" + str(i)
    driver.get(url)
    print(f"Opening first state {url}")
    #driver.maximize_window()
    
    #DEALERS
    res = driver.page_source.encode('utf-8')
    soup = BeautifulSoup(res, "html.parser")
    
    nr_dealers = len(soup.find(attrs = {"id": "dealers-list"}).find_all(attrs ={"class": "sds-container dealer-card"}))
    #check total nr of dealers and set max 25 iterations
    if nr_dealers >= 25:
        max_iter = 25
    else:
        max_iter = nr_dealers
    #iterate through the nr of dealers
    for j in range(0, max_iter):
        print('TAKE DEALER', j)
        dealers_data = dealers(soup, j) #call function
        dealers_data['state'] = codes['State'][x]
        dealers_data['dealer_id'] = str(uuid4()) #create unique id
        write_dealer(dealers_data)
        
        #CARS of each dealer
        #check if there is inventory
        if pd.isna(dealers_data['inventory_link']) is False:
            #update url to show more cars on a page
            inventory_link = dealers_data['inventory_link'] + '?page=1&page_size=72'
            url = inventory_link
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")
            
            #nr pages
            pages = soup.find(attrs = {"class": "sds-pagination__list"})
            nr_pages = len(pages.find_all("li"))
            current_page = 1

            while current_page <= nr_pages:
                #nr of cars on page
                car_list = soup.find_all(attrs = {"class": "shop-card shop-card-mobile-vertical-desktop-vertical"})
                for k in range(len(car_list)):
                    print('take car', k)
                    cars_data = cars(car_list, k) #call function
                    cars_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                    write_car(cars_data)

                #continue iteration over remaining pages
                current_page = current_page + 1
                inventory_link = dealers_data['inventory_link'] + '?page=' + str(current_page) + '&page_size=72'
                url = inventory_link
                driver.get(url)
                res = driver.page_source.encode('utf-8')
                soup = BeautifulSoup(res, "html.parser")
            
        #REVIEWS of each dealer
        if pd.isna(dealers_data['nr_reviews']) is False:
            reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=1&page_size=40&sort_by=MostRecent#review-sort-by'
            url = reviews_link
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")

            #calculate limit of reviews to collect
            limit = calculate(dealers_data['nr_reviews'], dealers_data['inventory_size'])
            filter_limit = limit//4
            #---------------------------------------------------------------------------------------------
            #most recent
            print("MOST RECENT")
            counter = 0 #count reviews of each page
            current_page = 1
            k = 1 #count total reviews
            while k <= filter_limit: #take all reviews until limit
                print('take k review', k)
                print('take counter review of page', counter, current_page)
                reviews_data = reviews(soup, counter, current_page, url) #call function
                reviews_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                write_review(reviews_data)
                counter = counter + 1 #add one review to counter
                k = k + 1
                if counter >= 40: #if we exceed the 40th review from a page
                    current_page = current_page + 1 #move on to next page
                    reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=' + str(current_page) + '&page_size=40&sort_by=MostRecent#review-sort-by'
                    url = reviews_link
                    driver.get(url)
                    res = driver.page_source.encode('utf-8')
                    soup = BeautifulSoup(res, "html.parser")
                    counter = 0 #reset review counter
            #---------------------------------------------------------------------------------------------        
            #lowest rated  
            print("LOWEST RATED")
            reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=1&page_size=40&sort_by=LowestRated#review-sort-by'
            url = reviews_link
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")
            counter = 0 #count reviews of each page
            current_page = 1
            k = 1 #count total reviews
            while k <= filter_limit: #take all reviews until limit
                print('take k review', k)
                print('take counter review of page', counter, current_page)
                reviews_data = reviews(soup, counter, current_page, url) #call function
                reviews_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                write_review(reviews_data)
                counter = counter + 1 #add one review to counter
                k = k + 1
                if counter >= 40: #if we exceed the 40th review from a page
                    current_page = current_page + 1 #move on to next page
                    reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=' + str(current_page) + '&page_size=40&sort_by=LowestRated#review-sort-by'
                    url = reviews_link
                    driver.get(url)
                    res = driver.page_source.encode('utf-8')
                    soup = BeautifulSoup(res, "html.parser")
                    counter = 0 #reset review counter 
            #--------------------------------------------------------------------------------------------
            #most helpful 
            print("MOST HELPFUL")
            reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=1&page_size=40&sort_by=MostHelpful#review-sort-by'
            url = reviews_link
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")
            counter = 0 #count reviews of each page
            current_page = 1
            k = 1 #count total reviews
            while k <= filter_limit: #take all reviews until limit
                print('take k review', k)
                print('take counter review of page', counter, current_page)
                reviews_data = reviews(soup, counter, current_page, url) #call function
                reviews_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                write_review(reviews_data)
                counter = counter + 1 #add one review to counter
                k = k + 1
                if counter >= 40: #if we exceed the 40th review from a page
                    current_page = current_page + 1 #move on to next page
                    reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=' + str(current_page) + '&page_size=40&sort_by=MostHelpful#review-sort-by'
                    url = reviews_link
                    driver.get(url)
                    res = driver.page_source.encode('utf-8')
                    soup = BeautifulSoup(res, "html.parser")
                    counter = 0 #reset review counter 
            #--------------------------------------------------------------------------------------------
            #highest rated 
            print("HIGHEST RATED")
            reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=1&page_size=40&sort_by=HighestRated#review-sort-by'
            url = reviews_link
            driver.get(url)
            res = driver.page_source.encode('utf-8')
            soup = BeautifulSoup(res, "html.parser")
            counter = 0 #count reviews of each page
            current_page = 1
            k = 1 #count total reviews
            while k <= filter_limit: #take all reviews until limit
                print('take k review', k)
                print('take counter review of page', counter, current_page)
                reviews_data = reviews(soup, counter, current_page, url) #call function
                reviews_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                write_review(reviews_data)
                counter = counter + 1 #add one review to counter
                k = k + 1
                if counter >= 40: #if we exceed the 40th review from a page
                    current_page = current_page + 1 #move on to next page
                    reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=' + str(current_page) + '&page_size=40&sort_by=HighestRated#review-sort-by'
                    url = reviews_link
                    driver.get(url)
                    res = driver.page_source.encode('utf-8')
                    soup = BeautifulSoup(res, "html.parser")
                    counter = 0 #reset review counter 
                    
        #go back to first page to move to next dealer
        url = "https://www.cars.com/dealers/buy/?makes[]=&maximum_distance=99999&page=1&page_size=100&zip=" + str(i)
        driver.get(url)   
        res = driver.page_source.encode('utf-8')
        soup = BeautifulSoup(res, "html.parser")
    
end_time = time.time()
print("time elapsed: ", end_time-start_time)  

Opening first state https://www.cars.com/dealers/buy/?makes[]=&maximum_distance=99999&page=1&page_size=100&zip=57001
TAKE DEALER 0
writing dealer into file
take car 0
writing car into file
take car 1
writing car into file
take car 2
writing car into file
take car 3
writing car into file
take car 4
writing car into file
take car 5
writing car into file
take car 6
writing car into file
take car 7
writing car into file
take car 8
writing car into file
take car 9
writing car into file
take car 10
writing car into file
take car 11
writing car into file
take car 12
writing car into file
take car 13
writing car into file
take car 14
writing car into file
take car 15
writing car into file
take car 16
writing car into file
take car 17
writing car into file
take car 18
writing car into file
take car 19
writing car into file
take car 20
writing car into file
take car 21
writing car into file
take car 22
writing car into file
take car 23
writing car into file
take car 24
writing car into file
take

take car 0
writing car into file
MOST RECENT
take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
LOWEST RATED
take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
MOST HELPFUL
take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
HIGHEST RATED
take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
TAKE DEALER 2
writing dealer into file


take car 0
writing car into file
take car 1
writing car into file
take car 2
writing car into file
take car 3
writing car into file
take car 4
writing car into file
take car 5
writing car into file
take car 6
writing car into file
take car 7
writing car into file
take car 8
writing car into file
take car 9
writing car into file
take car 10
writing car into file
take car 11
writing car into file
take car 12
writing car into file
take car 13
writing car into file
take car 14
writing car into file
take car 15
writing car into file
take car 16
writing car into file
take car 17
writing car into file
take car 18
writing car into file
take car 19
writing car into file
take car 20
writing car into file
take car 21
writing car into file
take car 22
writing car into file
take car 23
writing car into file
take car 24
writing car into file
take car 25
writing car into file
take car 26
writing car into file
take car 27
writing car into file
take car 28
writing car into file
take car 29
writing car 

take car 0
writing car into file
take car 1
writing car into file
take car 2
writing car into file
take car 3
writing car into file
take car 4
writing car into file
MOST RECENT
take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
take k review 4
take counter review of page 3 1
writing review into file
take k review 5
take counter review of page 4 1
writing review into file
take k review 6
take counter review of page 5 1
writing review into file
take k review 7
take counter review of page 6 1
writing review into file
take k review 8
take counter review of page 7 1
writing review into file
take k review 9
take counter review of page 8 1
writing review into file
take k review 10
take counter review of page 9 1
writing review into file
take k review 11
take counter review of page 10 1
writing review into file
take k review 12


writing review into file
take k review 35
take counter review of page 34 1
writing review into file
take k review 36
take counter review of page 35 1
writing review into file
take k review 37
take counter review of page 36 1
writing review into file
take k review 38
take counter review of page 37 1
writing review into file
take k review 39
take counter review of page 38 1
writing review into file
take k review 40
take counter review of page 39 1
writing review into file
take k review 41
take counter review of page 0 2
writing review into file
take k review 42
take counter review of page 1 2
writing review into file
take k review 43
take counter review of page 2 2
writing review into file
take k review 44
take counter review of page 3 2
writing review into file
take k review 45
take counter review of page 4 2
writing review into file
take k review 46
take counter review of page 5 2
writing review into file
take k review 47
take counter review of page 6 2
writing review into file
take k 

...

take k review 121
take counter review of page 0 4
writing review into file
take k review 122
take counter review of page 1 4
writing review into file
take k review 123
take counter review of page 2 4
writing review into file
take k review 124
take counter review of page 3 4
writing review into file
take k review 125
take counter review of page 4 4
writing review into file
take k review 126
take counter review of page 5 4
writing review into file
take k review 127
take counter review of page 6 4
writing review into file
take k review 128
take counter review of page 7 4
writing review into file
take k review 129
take counter review of page 8 4
writing review into file
take k review 130
take counter review of page 9 4
writing review into file
take k review 131
take counter review of page 10 4
writing review into file
take k review 132
take counter review of page 11 4
writing review into file
take k review 133
take counter review of page 12 4
writing review into file
take k review 134
take

writing review into file
take k review 90
take counter review of page 9 3
writing review into file
take k review 91
take counter review of page 10 3
writing review into file
take k review 92
take counter review of page 11 3
writing review into file
take k review 93
take counter review of page 12 3
writing review into file
take k review 94
take counter review of page 13 3
writing review into file
take k review 95
take counter review of page 14 3
writing review into file
take k review 96
take counter review of page 15 3
writing review into file
take k review 97
take counter review of page 16 3
writing review into file
take k review 98
take counter review of page 17 3
writing review into file
take k review 99
take counter review of page 18 3
writing review into file
take k review 100
take counter review of page 19 3
writing review into file
take k review 101
take counter review of page 20 3
writing review into file
take k review 102
take counter review of page 21 3
writing review into fil

writing review into file
take k review 59
take counter review of page 18 2
writing review into file
take k review 60
take counter review of page 19 2
writing review into file
take k review 61
take counter review of page 20 2
writing review into file
take k review 62
take counter review of page 21 2
writing review into file
take k review 63
take counter review of page 22 2
writing review into file
take k review 64
take counter review of page 23 2
writing review into file
take k review 65
take counter review of page 24 2
writing review into file
take k review 66
take counter review of page 25 2
writing review into file
take k review 67
take counter review of page 26 2
writing review into file
take k review 68
take counter review of page 27 2
writing review into file
take k review 69
take counter review of page 28 2
writing review into file
take k review 70
take counter review of page 29 2
writing review into file
take k review 71
take counter review of page 30 2
writing review into file


writing review into file
take k review 28
take counter review of page 27 1
writing review into file
take k review 29
take counter review of page 28 1
writing review into file
take k review 30
take counter review of page 29 1
writing review into file
take k review 31
take counter review of page 30 1
writing review into file
take k review 32
take counter review of page 31 1
writing review into file
take k review 33
take counter review of page 32 1
writing review into file
take k review 34
take counter review of page 33 1
writing review into file
take k review 35
take counter review of page 34 1
writing review into file
take k review 36
take counter review of page 35 1
writing review into file
take k review 37
take counter review of page 36 1
writing review into file
take k review 38
take counter review of page 37 1
writing review into file
take k review 39
take counter review of page 38 1
writing review into file
take k review 40
take counter review of page 39 1
writing review into file


writing review into file
take k review 138
take counter review of page 17 4
writing review into file
take k review 139
take counter review of page 18 4
writing review into file
take k review 140
take counter review of page 19 4
writing review into file
take k review 141
take counter review of page 20 4
writing review into file
take k review 142
take counter review of page 21 4
writing review into file
take k review 143
take counter review of page 22 4
writing review into file
take k review 144
take counter review of page 23 4
writing review into file
take k review 145
take counter review of page 24 4
writing review into file
take k review 146
take counter review of page 25 4
writing review into file
time elapsed:  21122.158099889755


In [98]:
x

49

In [62]:
dealer = soup.find(attrs = {"id": "dealers-list"}).find_all(attrs ={"class": "sds-container dealer-card"})[5]

In [64]:
dealer.find(attrs ={"class": "sds-rating__count"})

In [90]:
#reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=1&page_size=40&sort_by=HighestRated#review-sort-by'
#url = reviews_link
url = 'https://www.cars.com/dealers/182939/sunnyside-acura/reviews/?page=1&page_size=40&sort_by=HighestRated#review-sort-by'
driver.get(url)
res = driver.page_source.encode('utf-8')
soup = BeautifulSoup(res, "html.parser")

In [51]:
nr_dealers = len(soup.find(attrs = {"id": "dealers-list"}).find_all(attrs ={"class": "sds-container dealer-card"}))
    #check total nr of dealers and set max 25 iterations
if nr_dealers >= 25:
    max_iter = 25
else:
    max_iter = nr_dealers
max_iter        

25

In [81]:
current_page

3

In [91]:
counter = 0 #count reviews of each page
current_page = 1
k = 1 #count total reviews
while k <= filter_limit: #take all reviews until limit
                print('take k review', k)
                print('take counter review of page', counter, current_page)
                reviews_data = reviews(soup, counter, current_page, url) #call function
                reviews_data['dealer_id'] = dealers_data['dealer_id'] #add dealer id
                write_review(reviews_data)
                counter = counter + 1 #add one review to counter
                k = k + 1
                if counter >= 40: #if we exceed the 40th review from a page
                    current_page = current_page + 1 #move on to next page
                    reviews_link = str(dealers_data['dealer_link']) + 'reviews/?page=' + str(current_page) + '&page_size=40&sort_by=HighestRated#review-sort-by'
                    url = reviews_link
                    driver.get(url)
                    res = driver.page_source.encode('utf-8')
                    soup = BeautifulSoup(res, "html.parser")
                    counter = 0 #reset review counter 

take k review 1
take counter review of page 0 1
writing review into file
take k review 2
take counter review of page 1 1
writing review into file
take k review 3
take counter review of page 2 1
writing review into file
take k review 4
take counter review of page 3 1
writing review into file
take k review 5
take counter review of page 4 1
writing review into file
take k review 6
take counter review of page 5 1
writing review into file
take k review 7
take counter review of page 6 1
writing review into file
take k review 8
take counter review of page 7 1
writing review into file
take k review 9
take counter review of page 8 1
writing review into file
take k review 10
take counter review of page 9 1
writing review into file
take k review 11
take counter review of page 10 1
writing review into file
take k review 12
take counter review of page 11 1
writing review into file
take k review 13
take counter review of page 12 1
writing review into file
take k review 14
take counter review of page

writing review into file
take k review 111
take counter review of page 30 3
writing review into file
take k review 112
take counter review of page 31 3
writing review into file
take k review 113
take counter review of page 32 3
writing review into file
take k review 114
take counter review of page 33 3
writing review into file
take k review 115
take counter review of page 34 3
writing review into file
take k review 116
take counter review of page 35 3
writing review into file
take k review 117
take counter review of page 36 3
writing review into file
take k review 118
take counter review of page 37 3
writing review into file
take k review 119
take counter review of page 38 3
writing review into file
take k review 120
take counter review of page 39 3
writing review into file
take k review 121
take counter review of page 0 4
writing review into file
take k review 122
take counter review of page 1 4
writing review into file
take k review 123
take counter review of page 2 4
writing review 